In [1]:
import tensorflow as tf 
import numpy as np 
from tensorflow import keras 
import os 
import math 
import random 
import pickle 
import matplotlib.pyplot as plt 
from collections import deque 
from tensorflow.keras import layers
import time 

from vehicle_model_DDPG5_3 import Environment 
from cell_model import CellModel 

os.environ['CUDA_VISIBLE_DEVICES'] = '-1'

In [2]:
drving_cycle = '../../OC_SIM_DB/OC_SIM_DB_Cycles/Highway/01_FTP72_fuds.mat'
battery_path = "../../OC_SIM_DB/OC_SIM_DB_Bat/OC_SIM_DB_Bat_e-4wd_Battery.mat"
motor_path = "../../OC_SIM_DB/OC_SIM_DB_Mot/OC_SIM_DB_Mot_id_75_110_Westinghouse.mat"
cell_model = CellModel()
env = Environment(cell_model, drving_cycle, battery_path, motor_path, 10)

num_states = 5

In [3]:
class OUActionNoise: 
    def __init__(self, mean, std_deviation, theta=0.15, dt=1e-2, x_initial=None): 
        self.theta = theta 
        self.mean = mean 
        self.std_dev = std_deviation 
        self.dt = dt 
        self.x_initial = x_initial 
        self.reset() 
        
    def reset(self): 
        if self.x_initial is not None: 
            self.x_prev = self.x_initial 
        else: 
            self.x_prev = 0 
            
    def __call__(self): 
        x = (
             self.x_prev + self.theta * (self.mean - self.x_prev) * self.dt 
            + self.std_dev * np.sqrt(self.dt) * np.random.normal() 
        )
        self.x_prev = x 
        return x 

In [4]:
class Buffer: 
    def __init__(self, buffer_capacity=100000, batch_size=64): 
        self.maxs = np.zeros(num_states) 
        self.mins = np.zeros(num_states)
        
        self.buffer_capacity = buffer_capacity 
        self.batch_size = batch_size 
        self.buffer_counter = 0 
        
        self.state_buffer = np.zeros((self.buffer_capacity, num_states))
        self.action_buffer = np.zeros((self.buffer_capacity, 1))
        self.reward_buffer = np.zeros((self.buffer_capacity, 1))
        self.next_state_buffer = np.zeros((self.buffer_capacity, num_states))
        
    def record(self, obs_tuple): 
        index = self.buffer_counter % self.buffer_capacity 
        cur_state = np.array(obs_tuple[0])  
        
        self.maxs[cur_state > self.maxs] = cur_state[cur_state > self.maxs]
        self.mins[cur_state < self.mins] = cur_state[cur_state < self.mins]
            
        self.state_buffer[index] = obs_tuple[0]
        self.action_buffer[index] = obs_tuple[1]
        self.reward_buffer[index] = obs_tuple[2]
        self.next_state_buffer[index] = obs_tuple[3]
        
        self.buffer_counter += 1 
        
    def learn(self): 
        record_range = min(self.buffer_counter, self.buffer_capacity)
        batch_indices = np.random.choice(record_range, self.batch_size)
        
        state_batch = (self.state_buffer[batch_indices] - self.mins) / (self.maxs - self.mins)
        next_state_batch = (self.next_state_buffer[batch_indices] - self.mins) / (self.maxs - 
                                                                                  self.mins)
#         print(state_batch)
        
        state_batch = tf.convert_to_tensor(state_batch)
        action_batch = tf.convert_to_tensor(self.action_buffer[batch_indices])
        reward_batch = tf.convert_to_tensor(self.reward_buffer[batch_indices])
        reward_batch = tf.cast(reward_batch, dtype=tf.float32)
        next_state_batch = tf.convert_to_tensor(next_state_batch)
        
        with tf.GradientTape() as tape: 
            target_actions = target_actor(next_state_batch)
            y = reward_batch + gamma * target_critic([next_state_batch, target_actions])
            critic_value = critic_model([state_batch, action_batch])
            critic_loss = tf.math.reduce_mean(tf.square(y - critic_value)) 
        critic_grad = tape.gradient(critic_loss, critic_model.trainable_variables) 
        critic_optimizer.apply_gradients(
            zip(critic_grad, critic_model.trainable_variables)
        )
        
        with tf.GradientTape() as tape: 
            actions = actor_model(state_batch)
            critic_value = critic_model([state_batch, actions])
            actor_loss = - tf.math.reduce_mean(critic_value)
        actor_grad = tape.gradient(actor_loss, actor_model.trainable_variables) 
        actor_optimizer.apply_gradients(
            zip(actor_grad, actor_model.trainable_variables)
        )
        

In [5]:
def update_target(tau): 
    new_weights = [] 
    target_variables = target_critic.weights
    for i, variable in enumerate(critic_model.weights): 
        new_weights.append(target_variables[i] * (1 - tau) + tau * variable)
    target_critic.set_weights(new_weights)
    
    new_weights = [] 
    target_variables = target_actor.weights
    for i, variable in enumerate(actor_model.weights): 
        new_weights.append(target_variables[i] * (1 - tau) + tau * variable)
    target_actor.set_weights(new_weights)
    

In [6]:
def get_actor(): 
    last_init = tf.random_uniform_initializer(minval=-0.003, maxval=0.003)
    
    inputs = layers.Input(shape=(num_states))
    out = layers.Dense(512, activation="relu")(inputs)
#     out = layers.BatchNormalization()(out)
    out = layers.Dense(512, activation="relu")(out)
#     out = layers.BatchNormalization()(out)
    outputs = layers.Dense(1, activation="sigmoid", 
                          kernel_initializer=last_init)(out)
    model = tf.keras.Model(inputs, outputs)
    return model

In [7]:
def get_critic(): 
    state_input = layers.Input(shape=(num_states))
    state_out = layers.Dense(16, activation="relu")(state_input)
#     state_out = layers.BatchNormalization()(state_out)
    state_out = layers.Dense(32, activation="relu")(state_input)
#     state_out = layers.BatchNormalization()(state_out)
    
    action_input = layers.Input(shape=(1))
    action_out = layers.Dense(32, activation="relu")(action_input)
#     action_out = layers.BatchNormalization()(action_out)
    
    concat = layers.Concatenate()([state_out, action_out]) 
    
    out = layers.Dense(512, activation="relu")(concat)
#     out = layers.BatchNormalization()(out)
    out = layers.Dense(512, activation="relu")(out)
#     out = layers.BatchNormalization()(out)
    outputs = layers.Dense(1)(out)
    
    model = tf.keras.Model([state_input, action_input], outputs)
    return model 
    

In [8]:
def policy(state, noise_object): 
    j_min = state[0][2].numpy()
    j_max = state[0][3].numpy()
    sampled_action = tf.squeeze(actor_model(state)) 
    noise = noise_object()
    sampled_action = sampled_action.numpy() + noise 
    legal_action = sampled_action * j_max 
    legal_action = np.clip(legal_action, j_min, j_max)
#     print(j_min, j_max, legal_action, noise)
    return legal_action 
    

In [9]:
def policy_epsilon_greedy(state, eps): 
    j_min = state[0][-2].numpy()
    j_max = state[0][-1].numpy()
    
    if random.random() < eps: 
        a = random.randint(0, 9)
        return np.linspace(j_min, j_max, 10)[a]
    else: 
        sampled_action = tf.squeeze(actor_model(state)).numpy()  
        legal_action = sampled_action * j_max 
        legal_action = np.clip(legal_action, j_min, j_max)
        return legal_action

In [10]:
std_dev = 0.2 
ou_noise = OUActionNoise(mean=0, std_deviation=0.2)

actor_model = get_actor() 
critic_model = get_critic() 

target_actor = get_actor() 
target_critic = get_critic() 
target_actor.set_weights(actor_model.get_weights())
target_critic.set_weights(critic_model.get_weights())

critic_lr = 0.0002 
actor_lr = 0.0002 
critic_optimizer = tf.keras.optimizers.Adam(critic_lr)
actor_optimizer = tf.keras.optimizers.Adam(actor_lr)

total_episodes = 200 
gamma = 0.95 
tau = 0.001 

MAX_EPSILON = 1 
MIN_EPSILON = 0.01 
DECAY_RATE = 0.00002
BATCH_SIZE = 32 
DELAY_TRAINING = 3000 

In [11]:
print(env.version)

buffer = Buffer(500000, BATCH_SIZE)
eps = MAX_EPSILON 
steps = 0 

episode_rewards = [] 
episode_SOCs = [] 
episode_FCs = [] 
for ep in range(total_episodes): 
    start = time.time() 
    state = env.reset() 
    episodic_reward = 0 
    
    while True: 
        tf_state = tf.expand_dims(tf.convert_to_tensor(state), 0)
        action = policy_epsilon_greedy(tf_state, eps)
#         print(action)
        next_state, reward, done = env.step(action)
        if done: 
            next_state = [0] * num_states 
        
        buffer.record((state, action, reward, next_state))
        episodic_reward += reward 
        
        if steps > DELAY_TRAINING: 
            buffer.learn() 
            update_target(tau)
            eps = MIN_EPSILON + (MAX_EPSILON - MIN_EPSILON) * np.exp(-DECAY_RATE * steps)
        
        steps += 1
        
        if done: 
            break 
        
        state = next_state 
    
    elapsed_time = time.time() - start 
    print("elapsed_time: {:.3f}".format(elapsed_time))
    episode_rewards.append(episodic_reward) 
    episode_SOCs.append(env.SOC)
    episode_FCs.append(env.fuel_consumption) 
    
#     print("Episode * {} * Avg Reward is ==> {}".format(ep, avg_reward))
    SOC_deviation_history = np.sum(np.abs(np.array(env.history["SOC"]) - 0.6)) 
    print(
          'Episode: {}'.format(ep + 1),
          "Exploration P: {:.4f}".format(eps),
          'Total reward: {}'.format(episodic_reward), 
          "SOC: {:.4f}".format(env.SOC), 
          "Cumulative_SOC_deviation: {:.4f}".format(SOC_deviation_history), 
          "Fuel Consumption: {:.4f}".format(env.fuel_consumption), 
    )

results_dict = {} 
results_dict["rewards"] = episode_rewards 
results_dict["SOCs"] = episode_SOCs
results_dict["FCs"] = episode_FCs

3
maximum steps, simulation is done ... 
elapsed_time: 19.170
Episode: 1 Exploration P: 1.0000 Total reward: -1028.1443358872755 SOC: 0.8175 Cumulative_SOC_deviation: 96.5750 Fuel Consumption: 62.3947
maximum steps, simulation is done ... 
elapsed_time: 19.883
Episode: 2 Exploration P: 1.0000 Total reward: -947.2586426843507 SOC: 0.7924 Cumulative_SOC_deviation: 88.6815 Fuel Consumption: 60.4433
[[0.48858447 0.01754386 0.88854676 0.03658537 1.        ]
 [0.48858447 0.         0.46241661 0.03658537 1.        ]
 [0.48858447 0.         0.13535949 0.03658537 1.        ]
 [0.97716895 0.1875     0.66699182 0.03658537 1.        ]
 [0.48858447 0.64364035 0.14276881 0.03658537 1.        ]
 [0.48858447 0.         0.49125493 0.03658537 1.        ]
 [0.70319635 0.25767544 0.3453917  0.03658537 1.        ]
 [0.43835616 0.30921053 0.28435938 0.03658537 1.        ]
 [0.59817352 0.01096491 0.71474344 0.03658537 1.        ]
 [0.44292237 0.51754386 0.36941576 0.03658537 1.        ]
 [0.48858447 0.      

  1.00000000e+00]]
[[0.85844749 0.06140351 0.8188608  0.03658537 1.        ]
 [0.48858447 0.45175439 0.54962896 0.03658537 1.        ]
 [0.48858447 0.         0.59331361 0.03658537 1.        ]
 [0.48858447 0.         0.23274176 0.03658537 1.        ]
 [0.23287671 0.37938596 0.67227959 0.03658537 1.        ]
 [0.48858447 0.         0.47745015 0.03658537 1.        ]
 [0.49771689 0.50328947 0.55943506 0.03658537 1.        ]
 [0.53881279 0.44298246 0.50142942 0.03658537 1.        ]
 [0.52968037 0.53070175 0.37903332 0.03658537 1.        ]
 [0.48858447 0.         0.86446695 0.03658537 1.        ]
 [0.47488584 0.99671053 0.21812266 0.03658537 1.        ]
 [0.36986301 0.00877193 0.37634775 0.03658537 1.        ]
 [0.48858447 0.         0.1824465  0.03658537 1.        ]
 [0.39269406 0.4254386  0.5079235  0.03658537 1.        ]
 [0.44292237 0.3004386  0.2876509  0.03658537 1.        ]
 [0.43378995 0.47258772 0.47386835 0.03658537 1.        ]
 [0.51598174 0.99890351 0.23402413 0.03658537 1.     

[[4.88584475e-01 0.00000000e+00 3.23211024e-01 3.65853659e-02
  1.00000000e+00]
 [4.79452055e-01 4.25438596e-01 4.53550649e-01 3.65853659e-02
  1.00000000e+00]
 [4.88584475e-01 5.03289474e-01 5.60572654e-01 3.65853659e-02
  1.00000000e+00]
 [4.97716895e-01 4.53947368e-01 3.84858094e-01 3.65853659e-02
  1.00000000e+00]
 [4.88584475e-01 0.00000000e+00 6.28520027e-01 3.65853659e-02
  1.00000000e+00]
 [5.84474886e-01 3.96929825e-01 6.54154340e-01 3.65853659e-02
  1.00000000e+00]
 [5.25114155e-01 9.67105263e-01 3.11962571e-01 3.65853659e-02
  1.00000000e+00]
 [3.69863014e-01 4.42982456e-01 4.52801182e-01 3.65853659e-02
  1.00000000e+00]
 [4.61187215e-01 9.47368421e-01 1.64729846e-01 3.65853659e-02
  1.00000000e+00]
 [5.52511416e-01 3.38815789e-01 5.01351327e-01 3.65853659e-02
  1.00000000e+00]
 [5.15981735e-01 3.03728070e-01 5.27705175e-01 3.65853659e-02
  1.00000000e+00]
 [4.88584475e-01 6.20614035e-01 7.91980688e-02 3.65853659e-02
  1.00000000e+00]
 [9.58904110e-01 2.45614035e-01 6.072013

 [0.89954338 0.26864035 0.58107365 0.03658537 1.        ]]
[[0.14155251 0.0252193  0.08077228 0.03658537 1.        ]
 [0.48858447 0.         0.47032275 0.03658537 1.        ]
 [0.57077626 0.43201754 0.13960283 0.03658537 1.        ]
 [0.92237443 0.04605263 0.10147478 0.03658537 1.        ]
 [0.47945205 0.40570175 0.49631214 0.03658537 1.        ]
 [0.78082192 0.34429825 0.89513753 0.03658537 1.        ]
 [0.53881279 0.97807018 0.12349893 0.03658537 1.        ]
 [0.48858447 0.         0.56476092 0.03658537 1.        ]
 [0.42922374 0.46710526 0.47690978 0.03658537 1.        ]
 [0.31506849 0.05263158 0.46406086 0.03658537 1.        ]
 [0.48858447 0.         0.49718423 0.03658537 1.        ]
 [0.49771689 0.39692982 0.22069297 0.03658537 1.        ]
 [0.53424658 0.46929825 0.39212166 0.03658537 1.        ]
 [0.78538813 0.3125     0.41177938 0.03658537 1.        ]
 [0.37442922 0.14144737 0.64425056 0.03658537 1.        ]
 [0.48858447 0.         0.24545921 0.03658537 1.        ]
 [0.48858447 

[[0.52968037 0.43201754 0.89443642 0.03658537 1.        ]
 [0.59817352 0.31030702 0.30365509 0.03658537 1.        ]
 [0.46118721 0.46710526 0.6595409  0.03658537 1.        ]
 [0.49315068 0.29166667 0.3005903  0.03658537 1.        ]
 [0.44292237 0.45723684 0.52162439 0.03658537 1.        ]
 [0.73059361 0.02631579 0.81795393 0.03658537 1.        ]
 [0.47945205 0.90899123 0.10902342 0.03658537 1.        ]
 [0.456621   0.43969298 0.39452102 0.03658537 1.        ]
 [0.543379   0.38815789 0.30106208 0.03658537 1.        ]
 [0.64383562 0.45504386 0.47010669 0.03658537 1.        ]
 [0.26484018 0.12390351 0.64492378 0.03658537 1.        ]
 [0.41552511 0.48574561 0.65286917 0.03658537 1.        ]
 [0.73059361 0.02631579 0.81795393 0.03658537 1.        ]
 [0.55707763 0.9002193  0.3274906  0.03658537 1.        ]
 [0.48858447 0.         0.33165204 0.03658537 1.        ]
 [0.00456621 0.20833333 0.09320993 0.03658537 1.        ]
 [0.48858447 0.         0.09887413 0.03658537 1.        ]
 [0.67123288 0

...

[[0.68493151 0.32127193 0.37092803 0.03658537 1.        ]
 [0.53424658 0.44078947 0.10019449 0.03658537 1.        ]
 [0.43378995 0.49451754 0.52284141 0.03658537 1.        ]
 [0.44292237 0.45723684 0.40469966 0.03658537 1.        ]
 [0.06392694 0.14144737 0.74647251 0.03658537 1.        ]
 [0.83561644 0.22916667 0.31110018 0.03658537 1.        ]
 [0.48858447 0.         0.46318497 0.03658537 1.        ]
 [0.70776256 0.02850877 0.67529959 0.03658537 1.        ]
 [0.50684932 0.82894737 0.44443529 0.03658537 1.        ]
 [0.48858447 0.3004386  0.30676085 0.03658537 1.        ]
 [0.26940639 0.         0.17514812 0.03658537 1.        ]
 [0.19178082 0.10635965 0.80002073 0.03658537 1.        ]
 [0.85388128 0.03508772 0.45522183 0.03658537 1.        ]
 [0.47488584 0.42872807 0.42372985 0.03658537 1.        ]
 [0.48858447 0.91008772 0.20532888 0.03658537 1.        ]
 [0.97716895 0.19188596 0.1562724  0.03658537 1.        ]
 [0.48858447 0.         0.38713308 0.03658537 1.        ]
 [0.30593607 0

 [0.8173516  0.39144737 0.50884401 0.03658537 1.        ]]
[[5.70776256e-01 3.77192982e-01 4.20826221e-01 3.65853659e-02
  1.00000000e+00]
 [2.83105023e-01 3.61842105e-01 2.78632894e-01 3.65853659e-02
  1.00000000e+00]
 [4.33789954e-01 4.76973684e-01 6.13444798e-01 3.65853659e-02
  1.00000000e+00]
 [4.88584475e-01 0.00000000e+00 4.45990269e-01 3.65853659e-02
  1.00000000e+00]
 [5.34246575e-01 4.69298246e-01 5.11160883e-01 3.65853659e-02
  1.00000000e+00]
 [3.19634703e-01 7.32456140e-01 5.21283007e-02 3.65853659e-02
  1.00000000e+00]
 [1.46001932e-16 2.28070175e-01 2.32913066e-01 3.65853659e-02
  1.00000000e+00]
 [4.52054795e-01 4.95614035e-01 4.27453589e-01 3.65853659e-02
  1.00000000e+00]
 [5.38812785e-01 9.78070175e-01 5.82542146e-02 3.65853659e-02
  1.00000000e+00]
 [4.88584475e-01 0.00000000e+00 4.78884024e-01 3.65853659e-02
  1.00000000e+00]
 [4.88584475e-01 0.00000000e+00 4.75113120e-01 3.65853659e-02
  1.00000000e+00]
 [4.74885845e-01 4.67105263e-01 4.38426849e-01 3.65853659e-02

 [0.48858447 0.         0.63847054 0.03658537 1.        ]]
[[0.59817352 0.         0.76755452 0.03658537 1.        ]
 [0.66210046 0.24671053 0.60698196 0.03658537 1.        ]
 [0.36073059 0.44517544 0.39431261 0.03658537 1.        ]
 [0.48401826 0.61732456 0.06587601 0.03658537 1.        ]
 [0.0456621  0.45394737 0.19603293 0.03658537 1.        ]
 [0.48858447 0.         0.90344764 0.03658537 1.        ]
 [0.43835616 0.40460526 0.53435612 0.03658537 1.        ]
 [0.62100457 0.4002193  0.41730282 0.03658537 1.        ]
 [0.10502283 0.04385965 0.99040538 0.03658537 1.        ]
 [0.48858447 0.         0.55892583 0.03658537 1.        ]
 [0.47031963 0.44078947 0.09922242 0.03658537 1.        ]
 [0.48401826 0.99671053 0.2252599  0.03658537 1.        ]
 [0.38812785 0.4495614  0.6753179  0.03658537 1.        ]
 [0.48858447 0.         0.14579005 0.03658537 1.        ]
 [0.48858447 0.         0.08243579 0.03658537 1.        ]
 [0.48401826 0.52083333 0.26250141 0.03658537 1.        ]
 [0.40639269 

 [0.57990868 0.38815789 0.52053411 0.03658537 1.        ]]
[[0.48858447 0.         0.47265567 0.03658537 1.        ]
 [0.46118721 0.55811404 0.34277471 0.03658537 1.        ]
 [0.36986301 0.44298246 0.56940705 0.03658537 1.        ]
 [0.52968037 0.43201754 0.67908566 0.03658537 1.        ]
 [0.6347032  0.25548246 0.67028456 0.03658537 1.        ]
 [0.48858447 0.         0.15356263 0.03658537 1.        ]
 [0.48858447 0.         0.21608116 0.03658537 1.        ]
 [0.00456621 0.11074561 0.19551594 0.03658537 1.        ]
 [0.66210046 0.24671053 0.60698196 0.03658537 1.        ]
 [0.33789954 0.45504386 0.41859114 0.03658537 1.        ]
 [0.00456621 0.28618421 0.18490968 0.03658537 1.        ]
 [0.41552511 0.45833333 0.38812996 0.03658537 1.        ]
 [0.00456621 0.09539474 0.22133283 0.03658537 1.        ]
 [0.50228311 0.3125     0.14964902 0.03658537 1.        ]
 [0.66666667 0.37938596 0.24352015 0.03658537 1.        ]
 [0.6347032  0.37280702 0.43965729 0.03658537 1.        ]
 [0.92237443 

KeyboardInterrupt: 